### Installing the openai SDK in our python kernel

In [0]:
%pip install openai==1.56.0

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/389.8 kB ? eta -:--:--
   ━━━━╺━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.0/389.8 kB 1.7 MB/s eta 0:00:01
   ━━━━━━━╺━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.7/389.8 kB 927.8 kB/s eta 0:00:01
   ━━━━━━━━━━━━╸━━━━━━━━━━━━━━━━━━━━━━━━━━━ 122.9/389.8 kB 1.4 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━╺━━━━━━━━━━━━━ 256.0/389.8 kB 1.8 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╸━━ 368.6/389.8 kB 2.1 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 389.8/389.8 kB 2.0 MB/s eta 0:00:00
  Attempting uninstall: openai
    Found existing installation: openai 1.69.0
    Not uninstalling openai at /databricks/python3/lib/python3.12/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-5ce7af77-0af8-495f-9849-7680af473f67
    Can't uninstall 'openai'. No files were found to uninstall.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


### Installing the databricks vectorsearch SDK


In [0]:
%pip install databricks-vectorsearch

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


### Restarting our python kernel

In [0]:
dbutils.library.restartPython()

# GenAI with Azure Databricks - Developing RAG System

### Loading the csv file into the DBFS (Databricks File System)

In [0]:
 %sh
 rm -r /dbfs/rag_lab
 mkdir /dbfs/rag_lab
 wget -O /dbfs/rag_lab/customer_faq.csv https://raw.githubusercontent.com/sachin365123/CSV-files-for-Data-Science-and-Machine-Learning/refs/heads/main/Telco-Customer-Churn.csv

--2025-08-06 12:20:03--  https://raw.githubusercontent.com/sachin365123/CSV-files-for-Data-Science-and-Machine-Learning/refs/heads/main/Telco-Customer-Churn.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.108.133, 185.199.109.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 8256998 (7.9M) [text/plain]
Saving to: ‘/dbfs/rag_lab/customer_faq.csv’

     0K .......... .......... .......... .......... ..........  0%  799K 10s
    50K .......... .......... .......... .......... ..........  1% 1.04M 9s
   100K .......... .......... .......... .......... ..........  1% 3.40M 7s
   150K .......... .......... .......... .......... ..........  2% 4.49M 5s
   200K .......... .......... .......... .......... ..........  3% 1.58M 5s
   250K .......... .......... .......... .......... ..........  3% 5.83M 5s
   300K .......... ..........

### Loading the csv file into a dataframe

In [0]:
from pyspark.sql.functions import *

df = spark.read.load('/rag_lab/customer_faq.csv', format='csv', header=True)
display(df.limit(10))
df.printSchema()

customerID gender SeniorCitizen Partner Dependents tenure PhoneService MultipleLines InternetService OnlineSecurity OnlineBackup DeviceProtection TechSupport StreamingTV StreamingMovies Contract PaperlessBilling PaymentMethod MonthlyCharges TotalCharges Churn Question Answer 7590-VHVEG Female 0 Yes No 1 No No phone service DSL No Yes No No No No Month-to-month Yes Electronic check 29.85 29.85 No Who is Peter Lynch? Peter Lynch is one of history's most successful investment managers and mutual fund experts. He managed Fidelity's Magellan Fund from 1977 to 1990, growing it from $20 million to $14 billion in assets with an average annual return of 29.2%. Lynch is renowned for his practical investment philosophy that emphasizes investing in what you understand and thorough company research. He authored several influential investment books including 'One Up on Wall Street' and 'Beating the Street' that made investing accessible to everyday people. 5575-GNVDE Male 0 No No 34 Yes No DSL Yes No Yes No No No One year No Mailed check 56.95 1889.5 No What was Peter Lynch's average annual return at the Magellan Fund? Peter Lynch achieved an average annual return of 29.2% during his 13-year tenure managing Fidelity's Magellan Fund from 1977 to 1990. This exceptional performance more than doubled the S&P 500's annual return of approximately 15% during the same period. Lynch's track record meant that an initial investment of $10,000 when he started would have grown to approximately $280,000 by his retirement. This 29.2% average annual return over such an extended period remains one of the best long-term performance records in investment management history and established Lynch as one of the most successful fund managers of all time. His ability to maintain this level of performance while the fund grew from $20 million to $14 billion makes his achievement even more remarkable. 3668-QPYBK Male 0 No No 2 Yes No DSL Yes Yes No No No No Month-to-month Yes Mailed check 53.85 108.15 Yes How did Peter Lynch's performance compare to the S&P 500? Peter Lynch's performance at the Magellan Fund significantly outpaced the S&P 500 index. During his 13-year tenure from 1977 to 1990, Lynch generated an average annual return of 29.2%, compared to the S&P 500's return of approximately 15% during the same period. Lynch outperformed the S&P 500 in 11 out of 13 years, often by substantial margins. When compounded over his entire management period, Lynch's performance resulted in a total return of approximately 2,700%, compared to about 570% for the S&P 500. This consistent outperformance across different market environments—including both bull and bear markets—distinguishes Lynch from many other fund managers whose success was limited to specific market conditions. 7795-CFOCW Male 0 No No 45 No No phone service DSL Yes No Yes Yes No No One year No Bank transfer (automatic) 42.3 1840.75 No How much did the Magellan Fund grow under Peter Lynch? Under Peter Lynch's management, the Magellan Fund experienced extraordinary growth in assets, expanding from approximately $20 million when he took over in 1977 to $14 billion when he retired in 1990. This 700-fold increase came from two sources: the exceptional investment returns Lynch generated (averaging 29.2% annually) and substantial inflows of new investor money attracted by the fund's outstanding performance. By the time Lynch retired, Magellan had become the largest mutual fund in the world. This massive asset growth made Lynch's continued performance all the more impressive, as managing larger sums typically makes it more difficult to find enough attractive opportunities to maintain high percentage returns. 9237-HQITU Female 0 No No 2 Yes No Fiber optic No No No No No No Month-to-month Yes Electronic check 70.7 151.65 Yes Did Peter Lynch ever have a losing year at the Magellan Fund? During his 13-year tenure managing the Magellan Fund from 1977 to 1990, Peter Lynch experienced only two years with negative returns: 

root
 |-- customerID: string (nullable = true)
 |-- gender: string (nullable = true)
 |-- SeniorCitizen: string (nullable = true)
 |-- Partner: string (nullable = true)
 |-- Dependents: string (nullable = true)
 |-- tenure: string (nullable = true)
 |-- PhoneService: string (nullable = true)
 |-- MultipleLines: string (nullable = true)
 |-- InternetService: string (nullable = true)
 |-- OnlineSecurity: string (nullable = true)
 |-- OnlineBackup: string (nullable = true)
 |-- DeviceProtection: string (nullable = true)
 |-- TechSupport: string (nullable = true)
 |-- StreamingTV: string (nullable = true)
 |-- StreamingMovies: string (nullable = true)
 |-- Contract: string (nullable = true)
 |-- PaperlessBilling: string (nullable = true)
 |-- PaymentMethod: string (nullable = true)
 |-- MonthlyCharges: string (nullable = true)
 |-- TotalCharges: string (nullable = true)
 |-- Churn: string (nullable = true)
 |-- Question: string (nullable = true)
 |-- Answer: string (nullable = true)



## Keep Question and Answer Columns, remove other columns 

In [0]:


# Select only the required columns
df = df.select("Question", "Answer")

# Display first 10 rows
display(df.limit(10))

# Print schema
df.printSchema()


Question Answer Who is Peter Lynch? Peter Lynch is one of history's most successful investment managers and mutual fund experts. He managed Fidelity's Magellan Fund from 1977 to 1990, growing it from $20 million to $14 billion in assets with an average annual return of 29.2%. Lynch is renowned for his practical investment philosophy that emphasizes investing in what you understand and thorough company research. He authored several influential investment books including 'One Up on Wall Street' and 'Beating the Street' that made investing accessible to everyday people. What was Peter Lynch's average annual return at the Magellan Fund? Peter Lynch achieved an average annual return of 29.2% during his 13-year tenure managing Fidelity's Magellan Fund from 1977 to 1990. This exceptional performance more than doubled the S&P 500's annual return of approximately 15% during the same period. Lynch's track record meant that an initial investment of $10,000 when he started would have grown to approximately $280,000 by his retirement. This 29.2% average annual return over such an extended period remains one of the best long-term performance records in investment management history and established Lynch as one of the most successful fund managers of all time. His ability to maintain this level of performance while the fund grew from $20 million to $14 billion makes his achievement even more remarkable. How did Peter Lynch's performance compare to the S&P 500? Peter Lynch's performance at the Magellan Fund significantly outpaced the S&P 500 index. During his 13-year tenure from 1977 to 1990, Lynch generated an average annual return of 29.2%, compared to the S&P 500's return of approximately 15% during the same period. Lynch outperformed the S&P 500 in 11 out of 13 years, often by substantial margins. When compounded over his entire management period, Lynch's performance resulted in a total return of approximately 2,700%, compared to about 570% for the S&P 500. This consistent outperformance across different market environments—including both bull and bear markets—distinguishes Lynch from many other fund managers whose success was limited to specific market conditions. How much did the Magellan Fund grow under Peter Lynch? Under Peter Lynch's management, the Magellan Fund experienced extraordinary growth in assets, expanding from approximately $20 million when he took over in 1977 to $14 billion when he retired in 1990. This 700-fold increase came from two sources: the exceptional investment returns Lynch generated (averaging 29.2% annually) and substantial inflows of new investor money attracted by the fund's outstanding performance. By the time Lynch retired, Magellan had become the largest mutual fund in the world. This massive asset growth made Lynch's continued performance all the more impressive, as managing larger sums typically makes it more difficult to find enough attractive opportunities to maintain high percentage returns. Did Peter Lynch ever have a losing year at the Magellan Fund? During his 13-year tenure managing the Magellan Fund from 1977 to 1990, Peter Lynch experienced only two years with negative returns: 1981 and 1990. The 1981 decline came during a broader market downturn caused by high inflation and interest rates, while the 1990 loss occurred during his final year as the market struggled with recession concerns. Notably, even in these down years, the Magellan Fund generally outperformed or matched the broader market indices. Lynch's ability to limit the number and magnitude of losing years was a key factor in his exceptional long-term performance record, demonstrating his skill at navigating various market environments while maintaining his fundamental, research-driven approach. How many stocks did Peter Lynch typically hold in the Magellan Fund? At its peak, Peter Lynch's Magellan Fund reportedly held positions in over 1,400 different stocks, an unusually high number compared to most mutual funds. This broad diversi

root
 |-- Question: string (nullable = true)
 |-- Answer: string (nullable = true)



### Creating an Azure OpenAI Client


In [0]:
from openai import AzureOpenAI
import json

### # Take these credentials from Azure AI Foundary -> Azure Open AI 
openai_endpoint = "https://august06azureaopeaiexportcont.openai.azure.com/"
openai_key = "47bx6N4h5wgJG8L4p9sHn0oFIiSdSS8mEOFApGdLQG5CZbsSXyoDJQQJ99BHACHYHv6XJ3w3AAABACOGWlvW"

client = AzureOpenAI(
    api_key = openai_key,
    api_version = "2024-02-15-preview",
    azure_endpoint = openai_endpoint
)

In [0]:
display(df)

Question Answer Who is Peter Lynch? Peter Lynch is one of history's most successful investment managers and mutual fund experts. He managed Fidelity's Magellan Fund from 1977 to 1990, growing it from $20 million to $14 billion in assets with an average annual return of 29.2%. Lynch is renowned for his practical investment philosophy that emphasizes investing in what you understand and thorough company research. He authored several influential investment books including 'One Up on Wall Street' and 'Beating the Street' that made investing accessible to everyday people. What was Peter Lynch's average annual return at the Magellan Fund? Peter Lynch achieved an average annual return of 29.2% during his 13-year tenure managing Fidelity's Magellan Fund from 1977 to 1990. This exceptional performance more than doubled the S&P 500's annual return of approximately 15% during the same period. Lynch's track record meant that an initial investment of $10,000 when he started would have grown to approximately $280,000 by his retirement. This 29.2% average annual return over such an extended period remains one of the best long-term performance records in investment management history and established Lynch as one of the most successful fund managers of all time. His ability to maintain this level of performance while the fund grew from $20 million to $14 billion makes his achievement even more remarkable. How did Peter Lynch's performance compare to the S&P 500? Peter Lynch's performance at the Magellan Fund significantly outpaced the S&P 500 index. During his 13-year tenure from 1977 to 1990, Lynch generated an average annual return of 29.2%, compared to the S&P 500's return of approximately 15% during the same period. Lynch outperformed the S&P 500 in 11 out of 13 years, often by substantial margins. When compounded over his entire management period, Lynch's performance resulted in a total return of approximately 2,700%, compared to about 570% for the S&P 500. This consistent outperformance across different market environments—including both bull and bear markets—distinguishes Lynch from many other fund managers whose success was limited to specific market conditions. How much did the Magellan Fund grow under Peter Lynch? Under Peter Lynch's management, the Magellan Fund experienced extraordinary growth in assets, expanding from approximately $20 million when he took over in 1977 to $14 billion when he retired in 1990. This 700-fold increase came from two sources: the exceptional investment returns Lynch generated (averaging 29.2% annually) and substantial inflows of new investor money attracted by the fund's outstanding performance. By the time Lynch retired, Magellan had become the largest mutual fund in the world. This massive asset growth made Lynch's continued performance all the more impressive, as managing larger sums typically makes it more difficult to find enough attractive opportunities to maintain high percentage returns. Did Peter Lynch ever have a losing year at the Magellan Fund? During his 13-year tenure managing the Magellan Fund from 1977 to 1990, Peter Lynch experienced only two years with negative returns: 1981 and 1990. The 1981 decline came during a broader market downturn caused by high inflation and interest rates, while the 1990 loss occurred during his final year as the market struggled with recession concerns. Notably, even in these down years, the Magellan Fund generally outperformed or matched the broader market indices. Lynch's ability to limit the number and magnitude of losing years was a key factor in his exceptional long-term performance record, demonstrating his skill at navigating various market environments while maintaining his fundamental, research-driven approach. How many stocks did Peter Lynch typically hold in the Magellan Fund? At its peak, Peter Lynch's Magellan Fund reportedly held positions in over 1,400 different stocks, an unusually high number compared to most mutual funds. This broad diversi

### Saving the updated/new dataframe into ADLS as parquet storage

In [0]:
%sql
show catalogs

catalog __databricks_internal catalogjuly22 devops_dlt_july22 health_catalyst_detecting_sudden_patient_satisfaction_anomalies hive_metastore main samples system

In [0]:
%sql
use catalog catalogjuly22

In [0]:
%sql
show databases

databaseName default devops_dlt_july22 information_schema sachin_dlt_july22

In [0]:
%sql
use database sachin_dlt_july22

In [0]:
# Save the updated DataFrame as a Parquet file or table
df.write.mode("overwrite").parquet("/rag_lab/customer_faq.parquet")
df.write.format("delta").mode("overwrite").saveAsTable("sachin_dlt_july22.diabetes_faq_table")


### Enabling Change Data Feed on Our Table

In [0]:
# Enable change data feed for the existing Delta table
spark.sql("""
ALTER TABLE catalogjuly22.sachin_dlt_july22.diabetes_faq_table
SET TBLPROPERTIES (delta.enableChangeDataFeed = true)
""")

DataFrame[]

### Developing the Cluster managed Vector index

In [0]:
from databricks.vector_search.client import VectorSearchClient

vector_client = VectorSearchClient()

vector_client.create_endpoint(
     name="vector_search_saxena_new123",
     endpoint_type="STANDARD"
 )

index = vector_client.create_delta_sync_index(
   endpoint_name="vector_search_saxena_new123",
   source_table_name="catalogjuly22.devops_dlt_july22.diabetes_faq_table",
   index_name="catalogjuly22.devops_dlt_july22.diabetes_faq_index",
   pipeline_type="TRIGGERED",
    #  Change below Column name with your first column name "Question"
   primary_key="Question",
  #  Change below Column name with your second column name "Answer"
   embedding_source_column="Answer",
   embedding_model_endpoint_name="databricks-gte-large-en"
  )

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.


# Now check, catalog -> catalogjuly22.devops_dlt_july22.diabetes_faq_index 
# and see that provision is in progress

### Once it is finished in 20 mins, ask run the following code

### Triggering our Vector Index - Information Retriever

In [0]:
user_question = "How did Peter Lynch's performance compare to the S&P 500?"

results_dict = index.similarity_search(
            query_text = "{user_question}",
            columns = ["Question", "Answer"],
            num_results=1
          )

content = str(results_dict['result']['data_array'][0])
print(content)

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.
["What are Peter Lynch's hobbies and interests?", "Outside of investing and philanthropy, Peter Lynch's personal interests and hobbies have included: 1) Tennis, which he has played regularly throughout his adult life for both exercise and relaxation; 2) Reading, particularly history, biographies, and business literature; 3) Traveling, which he has been able to enjoy more extensively since retirement; 4) Boston sports teams, especially the Red Sox; 5) Art appreciation, reflected in the Lynch Foundation's support for cultural institutions; and 6) Education, demonstrated through his ongoing involvement with educational institutions and teaching opportunities. Lynch has maintained a relatively private personal life, especially after retirement, but has mentioned that achieving better

### Developing the Generation Component of our RAG architecture


### Azure Portal → Azure Foundary → Create new instance -> click on this new model -> copy model name -> Deployments tab -> Deploy Modle GPT-4
### Give any other different name of Deployment Name eg "gpt-4.1-minisachin"
#### Other wise name error will be there

In [0]:
gpt_response = client.chat.completions.create(
                model="gpt-4.1-minisachinaug06", # model = "deployment_name".
                messages=[
                    {"role": "system", "content": "You are a helpful assistant. You will be passed the user query and the supporting knowledge that can be used to answer the user_query"},
                    {"role": "user", "content": f"user query : {user_question} and supporting knowledge: {content}"}
                ]
            )
print(gpt_response.choices[0].message.content)

Trace(request_id=tr-6696f6c944b74b3ba9670e3d9f86d16f)

---------------------------------------------------------------------------
NotFoundError                             Traceback (most recent call last)
File <command-5425188694401563>, line 1
----> 1 gpt_response = client.chat.completions.create(
      2                 model="gpt-4.1-minisachinaug06", # model = "deployment_name".
      3                 messages=[
      4                     {"role": "system", "content": "You are a helpful assistant. You will be passed the user query and the supporting knowledge that can be used to answer the user_query"},
      5                     {"role": "user", "content": f"user query : {user_question} and supporting knowledge: {content}"}
      6                 ]
      7             )
      8 print(gpt_response.choices[0].message.content)

File /databricks/python/lib/python3.12/site-packages/mlflow/utils/autologging_utils/safety.py:483, in safe_patch.<locals>.safe_patch_function(*args, **kwargs)
    479 call_original = update_wrapper_extended(

### Developing the RAG model

In [0]:
import mlflow
from mlflow import pyfunc
from openai import AzureOpenAI

class RAGModel(pyfunc.PythonModel):
      def __init__(self, vector_index):
          self.vector_index=vector_index
      
      def retrieve(self, query):
          results_dict = self.vector_index.similarity_search(
            query_text = query,
            columns = ["Question", "Answer"],
            num_results=1
          )

          return results_dict
        
      def chatCompletionsAPI(self, user_query, supporting_knowledge):
          openai_client = AzureOpenAI(
            ### # Take these credentials from Azure AI Foundary -> Azure Open AI
            azure_endpoint = "https://august06azureaopeaiexportcont.openai.azure.com/",
            api_key = "47bx6N4h5wgJG8L4p9sHn0oFIiSdSS8mEOFApGdLQG5CZbsSXyoDJQQJ99BHACHYHv6XJ3w3AAABACOGWlvW",
            api_version = "2024-02-15-preview"
           
          )

          response = openai_client.chat.completions.create(
                model="gpt-4.1-minisachin", # model = "deployment_name".
                messages=[
                    {"role": "system", "content": "You are a helpful assistant. You will be passed the user query and the supporting knowledge that can be used to answer the user_query"},
                    {"role": "user", "content": f"user query : {user_query} and supporting knowledge: {supporting_knowledge}"}
                ]
            )
          return response.choices[0].message.content
      
      def predict(self, context, data):
          query = data["query"].iloc[0]
          text_data = self.retrieve(query)
          return self.chatCompletionsAPI(query, text_data)
          


      

/databricks/python/lib/python3.12/site-packages/mlflow/pyfunc/utils/data_validation.py:155: FutureWarning: Model's `predict` method contains invalid parameters: {'data'}. Only the following parameter names are allowed: context, model_input, and params. Note that invalid parameters will no longer be permitted in future versions.
  param_names = _check_func_signature(func, "predict")
/databricks/python/lib/python3.12/site-packages/mlflow/pyfunc/utils/data_validation.py:186: UserWarning: Add type hints to the `predict` method to enable data validation and automatic signature inference during model logging. Check https://mlflow.org/docs/latest/model/python_model.html#type-hint-usage-in-pythonmodel for more details.
  color_warning(


### Saving our Model

In [0]:
test_model = RAGModel(vector_index=index)

In [0]:
from mlflow.models import infer_signature
import pandas as pd

signature = infer_signature(pd.DataFrame([{"query": "How did Peter Lynch's performance compare to the S&P 500?"}]))
model_path = "Sachinmodelnewaug06"
mlflow.pyfunc.save_model(path=model_path, python_model=test_model, signature=signature)

/databricks/python/lib/python3.12/site-packages/mlflow/pyfunc/__init__.py:3212: UserWarning: An input example was not provided when logging the model. To ensure the model signature functions correctly, specify the `input_example` parameter. See https://mlflow.org/docs/latest/model/signatures.html#model-input-example for more details about the benefits of using input_example.
  color_warning(


### Loading Our Saved Model

In [0]:
# Load our custom model from the local artifact store
loaded_pyfunc_model = mlflow.pyfunc.load_model(model_path)


### Testing our Loaded/Saved Model

In [0]:
model_input = pd.DataFrame([{"query": "How did Peter Lynch's performance compare to the S&P 500?"}])

model_response = loaded_pyfunc_model.predict(model_input)

print(model_response)

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.


Trace(request_id=tr-4badeae2d897497aba51f5cb8c47511f)

---------------------------------------------------------------------------
NotFoundError                             Traceback (most recent call last)
File <command-5425188694401572>, line 3
      1 model_input = pd.DataFrame([{"query": "How did Peter Lynch's performance compare to the S&P 500?"}])
----> 3 model_response = loaded_pyfunc_model.predict(model_input)
      5 print(model_response)

File /databricks/python/lib/python3.12/site-packages/mlflow/pyfunc/__init__.py:804, in PyFuncModel.predict(self, data, params)
    802 if schema := _get_dependencies_schema_from_model(self._model_meta):
    803     context.update(**schema)
--> 804 return self._predict(data, params)

File /databricks/python/lib/python3.12/site-packages/mlflow/pyfunc/__init__.py:854, in PyFuncModel._predict(self, data, params)
    852 params_arg = inspect.signature(self._predict_fn).parameters.get("params")
    853 if params_arg and params_arg.kind != inspect.Parameter.VAR_KEYWORD:
--> 854     return self._predict

### Logging our saved model as an artifact

In [0]:
import mlflow

# Log the model as an artifact
with mlflow.start_run() as run:
    mlflow.log_artifacts(local_dir=model_path, artifact_path="rag_model")
    print(f"Model logged with run ID: {run.info.run_id}")


Uploading artifacts:   0%|          | 0/5 [00:00<?, ?it/s]

Model logged with run ID: 23ee695b83e94c54b4a43cc4164d9b75


### Inferencing the real-time endpoint

### To view model: Now from left pane go to Workspace -> check your model name "Sachinmodelnew"

##### to run register this model locate from Logged 1 run to an experiment in MLflow. Learn more above run,
#### then register manually

### Now go to model and create end points manually

### Will take much time then use following code to check end points

In [0]:
{
  "dataframe_records":[
    {
        "query":"How did Peter Lynch's performance compare to the S&P 500?"
    }
  ]
}

{'dataframe_records': [{'query': "How did Peter Lynch's performance compare to the S&P 500?"}]}